In [1]:
# !pip install import_ipynb --quiet
# !pip install anvil-uplink --quiet
# !pip install yfinance --quiet
# !pip install pandas_ta --quiet
# !pip install ipynb --quiet
# !pip install rpyc --quiet
# !pip install stable-baselines3 --quiet
# !pip install aspectlib

In [2]:
# !git clone https://github.com/gmshroff/algostrats.git

In [3]:
# %cd algostrats

Uncomment below if on Colab and using datasets from Kaggle

In [4]:
# from google.colab import files
# uploaded=files.upload()

In [5]:
# !mkdir /root/.kaggle
# !mv ./kaggle.json /root/.kaggle/.
# !chmod 600 /root/.kaggle/kaggle.json

In [6]:
# %mkdir data
# %cd data
# !kaggle datasets download -d gmshroff/marketdatafivemin
# %cd ../algostrats

In [1]:
colab=False
script=False
if not colab: 
    DATAPATH='../algodata/'
elif colab: DATAPATH='../data/'

Need to import algorithms from stable-baselines3

In [2]:
from stable_baselines3 import PPO,A2C,DQN
from stable_baselines3.common.vec_env import StackedObservations
from stable_baselines3.common.monitor import Monitor as Mon

In [3]:
import warnings
warnings.simplefilter("ignore")

In [4]:
import import_ipynb
import pandas as pd
import numpy as np
import torch
from datetime import datetime
from datetime import datetime as dt
from torch.utils.data import Dataset
from sklearn.preprocessing import StandardScaler
import pickle
from threading import Thread
import threading
from IPython import display
import time,getopt,sys,os

In [5]:
from feeds import BackFeed,DataFeed
from featfuncs import feat_aug,add_addl_features_feed,add_ta_features_feed,add_sym_feature_feed
from featfuncs import add_global_indices_feed

importing Jupyter notebook from feeds.ipynb
importing Jupyter notebook from synfeed.ipynb
importing Jupyter notebook from india_calendar.ipynb
importing Jupyter notebook from featfuncs.ipynb


In [6]:
from feed_env import Episode
import aspectlib

importing Jupyter notebook from feed_env.ipynb


### Trading strategies as agents

RL(++)StratAgents imported from ruleagents<br>

In [7]:
from rlagents import RLStratAgentDyn, COLS, RLStratAgentDynFeatures

importing Jupyter notebook from rlagents.ipynb
importing Jupyter notebook from aiagentbase.ipynb


In [8]:
len(COLS)

21

### Strategy Development: Training RLStratAgent using BackTestWorld

In [9]:
from backtest import Backtest
from feeds import BackFeed,DataFeed
from validation import Validate
from add_features import add_features

importing Jupyter notebook from backtest.ipynb
importing Jupyter notebook from validation.ipynb


<b>Configuration for training RL model<b>

In [10]:
algorithm=PPO
synthetic=False #use synthetic data
simple='sinewave' #False,True or 'sinewave'
nd,nw=4,5 #for BackFeed

In [11]:
if script:
    try:
        opts,args = getopt.getopt(sys.argv[1:],"hl:f:d:m:s:w:t:p:u:",["load=","feed=","datafile=","modelname=","synthetic","weeks","training_steps","deploy","use_alt_data"])
    except getopt.GetoptError:
        print('rlagents_train.py -l <load:True/False> -f <scan:back/data> -d <datafile> -m <modelname> -s <synthetic> -w <weeks> -t <training_steps> -p <deploy>')
        sys.exit(2)
    load,feed,modelname=False,'back',''
    training_steps=50000 # if less then n_steps then n_steps is used
    deploy=True
    date=datetime.today().strftime('%d-%b-%Y')
    use_alt_data=False
    for opt, arg in opts:
        if opt == "-h":
            print('rlagents_train.py -l <load:True/False> -f <scan:back/data> -d <datafile> -m <modelname> -s <synthetic> -w <weeks> -t <training_steps> -p <deploy> -u <use_alt_data>')
            sys.exit()
        elif opt in ("-l", "--load"):
            load = (lambda x: True if x=='True' else False)(arg)
        elif opt in ("-f", "--feed"):
            feed = (lambda x: 'data' if x=='data' else 'back')(arg)
        elif opt in ("-d", "--datafile"):
            datafile = arg.split('/')[-1]
        elif opt in ("-m", "--modelname"):
            modelname = arg
        elif opt in ("-s", "--synthetic"):
            synthetic = (lambda x: True if x=='True' else False)(arg)
        elif opt in ("-w", "--weeks"):
            nw = int(arg)
        elif opt in ("-t", "--training_steps"):
            training_steps=int(arg)
        elif opt in ("-p", "--deploy"):
            deploy = (lambda x: True if x=='True' else False)(arg)
        elif opt in ("-u", "--use_alt_data"):
            use_alt_data = (lambda x: True if x=='True' else False)(arg)
    if len(opts)==0: 
        print('rlagents_train.py -l <load:True/False> -f <scan:back/data> -d <datafile> -m <modelname> -s <synthetic> -w <weeks> -t <training_steps> -p <deploy> -u <use_alt_data>')
        sys.exit()
    print(f"load:{load},feed:{feed},datafile:{datafile},modelname:{modelname},synthetic:{synthetic},weeks:{nw},training_steps:{training_steps},deploy:{deploy},use_alt_data:{use_alt_data}")
    loadfeed=load
    if feed=='data': datafeed=True
    else: datafeed=False

In [12]:
if not script:
    loadfeed=True
    datafeed=True
    datafile='realdata/alldata.csv'
    modelname='RLC0_all.pth'
    # modelname='SINE1.pth' # replace with modelname if model to be saved to saved_models
    # modelname='RLG0.pth'
    date=datetime.today().strftime('%d-%b-%Y')
    training_steps=500000 # if less then n_steps then n_steps is used
    deploy=True
    use_alt_data=False

In [13]:
n_steps=2048 # reduce for debugging only else 2048

In [14]:
def stringify(x):
    return pd.to_datetime(x['Datetime']).strftime('%d-%b-%Y')

In [15]:
ADD_FEATURES = False
RETAIN_OLD_FEATURES = True

In [16]:
import pickle
if not loadfeed and not datafeed:
    data=pd.read_csv('./capvolfiltered.csv')
    tickers=list(data.iloc[0:50]['ticker'].values)
    print('Creating feed')
    feed=BackFeed(tickers=tickers,nd=nd,nw=nw,interval='5m',synthetic=synthetic,simple=simple)
    print('Processing feed')
    add_addl_features_feed(feed,tickers=feed.tickers)
    add_sym_feature_feed(feed,tickers=feed.tickers)
    if not synthetic: add_global_indices_feed(feed)
    if not colab: 
        with open('../../temp_data/btfeed.pickle','wb') as f: pickle.dump(feed,f)
    elif colab: 
        with open('/tmp/btfeed.pickle','wb') as f: pickle.dump(feed,f)
elif loadfeed and not datafeed:
    if not colab: 
        with open('../../temp_data/btfeed.pickle','rb') as f: feed=pickle.load(f)
    elif colab: 
        with open('/tmp/btfeed.pickle','rb') as f: feed=pickle.load(f)

In [17]:
if not loadfeed and datafeed:
    DATAFILE=DATAPATH+datafile
    print('Reading datafile')
    df=pd.read_csv(DATAFILE)
    if 'Date' not in df.columns: 
        print('Adding Date')
        df['Date']=df.apply(stringify,axis=1)
    print('Creating feed')
    feed=DataFeed(tickers=list(df.ticker.unique()[0:10]),dfgiven=True,df=df)
    print('Processing feed')
    
    add_addl_features_feed(feed,tickers=feed.tickers)
    add_sym_feature_feed(feed,tickers=feed.tickers)
    # add_global_indices_feed(feed)

    if not colab: 
        with open(f'../algodata/realdata/datafeed_alldata_{RETAIN_OLD_FEATURES}_{ADD_FEATURES}.pkl','wb') as f: 
            pickle.dump(feed,f)
    elif colab: 
        with open('/tmp/btdatafeed.pickle','wb') as f: pickle.dump(feed,f)
        
        
elif loadfeed and datafeed:
    if not colab: 
        with open(f'../algodata/realdata/datafeed_alldata_{RETAIN_OLD_FEATURES}_{ADD_FEATURES}.pkl','rb') as f: feed=pickle.load(f)
    elif colab:
        with open('/tmp/btdatafeed.pickle','rb') as f: feed=pickle.load(f)

In [18]:
with open('additional_utils/cols.pkl', 'rb') as f:
        d = pickle.load(f)
        
# d['discrete_cols']+d['pre_discrete_cols']
imp_cols = d['imp_cols']
cols_to_use = d['cols_to_use']

In [19]:
feed.ndata['NELCAST.NS']['01-Apr-2022'].head(20)

Open       High        Low      Close  \
datetime                                                                
2022-03-31 09:15:00+05:30  60.700001  60.700001  61.200001  60.900002   
2022-03-31 09:20:00+05:30  60.900002  60.799999  60.950001  60.849998   
2022-03-31 09:26:00+05:30  60.849998  60.799999  60.849998  60.799999   
2022-03-31 09:31:00+05:30  60.700001  60.299999  60.799999  60.700001   
2022-03-31 09:36:00+05:30  61.000000  60.700001  61.000000  60.799999   
2022-03-31 09:41:00+05:30  60.799999  60.400002  60.799999  60.599998   
2022-03-31 09:46:00+05:30  60.599998  60.450001  60.700001  60.650002   
2022-03-31 09:52:00+05:30  60.500000  60.099998  60.500000  60.200001   
2022-03-31 09:57:00+05:30  60.000000  60.000000  60.349998  60.200001   
2022-03-31 10:03:00+05:30  60.200001  59.900002  60.200001  60.000000   
2022-03-31 10:08:00+05:30  60.000000  59.950001  60.349998  60.349998   
2022-03-31 10:13:00+05:30  60.349998  60.000000  60.400002  60.200001   
2022-03-31 10:20:00+05:30  59.900002  59.799999  60.150002  60.000000   
2022-03-31 10:26:00+05:30  60.049999  60.000000  60.500000  60.000000   
2022-03-31 10:32:00+05:30  60.000000  59.650002  60.049999  59.950001   
2022-03-31 10:41:00+05:30  59.950001  59.900002  60.150002  60.150002   
2022-03-31 10:47:00+05:30  60.099998  59.900002  60.150002  59.900002   
2022-03-31 10:54:00+05:30  60.049999  59.900002  60.200001  60.150002   
2022-03-31 10:59:00+05:30  60.150002  60.150002  60.299999  60.150002   
2022-03-31 11:04:00+05:30  60.150002  60.150002  60.349998  60.250000   

                            Volume                   Datetime      ticker  \
datetime                                                                    
2022-03-31 09:15:00+05:30   6007.0  2022-03-31 09:15:00+05:30  NELCAST.NS   
2022-03-31 09:20:00+05:30   1397.0  2022-03-31 09:20:00+05:30  NELCAST.NS   
2022-03-31 09:26:00+05:30    208.0  2022-03-31 09:26:00+05:30  NELCAST.NS   
2022-03-31 09:31:00+05:30  12607.0  2022-03-31 09:31:00+05:30  NELCAST.NS   
2022-03-31 09:36:00+05:30   3422.0  2022-03-31 09:36:00+05:30  NELCAST.NS   
2022-03-31 09:41:00+05:30   5064.0  2022-03-31 09:41:00+05:30  NELCAST.NS   
2022-03-31 09:46:00+05:30   1567.0  2022-03-31 09:46:00+05:30  NELCAST.NS   
2022-03-31 09:52:00+05:30   9175.0  2022-03-31 09:52:00+05:30  NELCAST.NS   
2022-03-31 09:57:00+05:30   4190.0  2022-03-31 09:57:00+05:30  NELCAST.NS   
2022-03-31 10:03:00+05:30   5402.0  2022-03-31 10:03:00+05:30  NELCAST.NS   
2022-03-31 10:08:00+05:30   2593.0  2022-03-31 10:08:00+05:30  NELCAST.NS   
2022-03-31 10:13:00+05:30   2684.0  2022-03-31 10:13:00+05:30  NELCAST.NS   
2022-03-31 10:20:00+05:30   8972.0  2022-03-31 10:20:00+05:30  NELCAST.NS   
2022-03-31 10:26:00+05:30   5304.0  2022-03-31 10:26:00+05:30  NELCAST.NS   
2022-03-31 10:32:00+05:30   5741.0  2022-03-31 10:32:00+05:30  NELCAST.NS   
2022-03-31 10:41:00+05:30   7985.0  2022-03-31 10:41:00+05:30  NELCAST.NS   
2022-03-31 10:47:00+05:30  11066.0  2022-03-31 10:47:00+05:30  NELCAST.NS   
2022-03-31 10:54:00+05:30  17022.0  2022-03-31 10:54:00+05:30  NELCAST.NS   
2022-03-31 10:59:00+05:30    842.0  2022-03-31 10:59:00+05:30  NELCAST.NS   
2022-03-31 11:04:00+05:30   3631.0  2022-03-31 11:04:00+05:30  NELCAST.NS   

                                  Date  Dividends  Stock Splits  ...  \
datetime                                                         ...   
2022-03-31 09:15:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:20:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:26:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:31:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:36:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:41:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:46:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31 09:52:00+05:30  31-Mar-2022        1.0           1.0  ...   
2022-03-31

In [20]:
ADD_FEATURES = True
using_cols = COLS + imp_cols

continuing_cols = using_cols + ['Date', 'datetime']

if ADD_FEATURES:
    for ticker in feed.data:
        df = feed.data[ticker]
        df, pre_discrete_cols, discrete_cols = add_features(df, columns_to_use=cols_to_use)
        feed.data[ticker] = df.loc[:, continuing_cols]

In [21]:
from india_calendar import IBDay

feed.ndata={}
for t in feed.tickers:
    print(f'[INFO] On ticker={t}')
    dfa=feed.data[t]
    dfL=[]
    feed.ndata[t]={}
    for d in dfa['Date'].unique():
        pdt=pd.to_datetime(d)
        pdtp=pdt-IBDay(1)
        df=dfa.loc[(pd.to_datetime(dfa['Date'])<=pdt)&
                    (pd.to_datetime(dfa['Date'])>=pdtp)]
        df['row_num'] = np.arange(len(df))
        df=df[~df.index.duplicated(keep='first')]
        df=df.sort_index()
        feed.ndata[t][d]=df

[INFO] On ticker=NELCAST.NS
[INFO] On ticker=AARTIDRUGS.NS
[INFO] On ticker=CYIENT.NS
[INFO] On ticker=HINDZINC.NS
[INFO] On ticker=TRENT.NS
[INFO] On ticker=TATAELXSI.NS
[INFO] On ticker=MINDTREE.NS
[INFO] On ticker=TI.NS
[INFO] On ticker=OBEROIRLTY.NS
[INFO] On ticker=SOMANYCERA.NS


In [22]:
feed.ndata['NELCAST.NS']['01-Apr-2022'].head(20)

row_num    Open_n    High_n     Low_n   Close_n  \
datetime                                                                     
2022-03-31 09:15:00+05:30        0  0.996716  0.996716  1.004926  1.000000   
2022-03-31 09:20:00+05:30        1  1.000000  0.998358  1.000821  0.999179   
2022-03-31 09:26:00+05:30        2  0.999179  0.998358  0.999179  0.998358   
2022-03-31 09:31:00+05:30        3  0.996716  0.990148  0.998358  0.996716   
2022-03-31 09:36:00+05:30        4  1.001642  0.996716  1.001642  0.998358   
2022-03-31 09:41:00+05:30        5  0.998358  0.991790  0.998358  0.995074   
2022-03-31 09:46:00+05:30        6  0.995074  0.992611  0.996716  0.995895   
2022-03-31 09:52:00+05:30        7  0.993432  0.986864  0.993432  0.988506   
2022-03-31 09:57:00+05:30        8  0.985222  0.985222  0.990969  0.988506   
2022-03-31 10:03:00+05:30        9  0.988506  0.983580  0.988506  0.985222   
2022-03-31 10:08:00+05:30       10  0.985222  0.984401  0.990969  0.990969   
2022-03-31 10:13:00+05:30       11  0.990969  0.985222  0.991790  0.988506   
2022-03-31 10:20:00+05:30       12  0.983580  0.981938  0.987685  0.985222   
2022-03-31 10:26:00+05:30       13  0.986043  0.985222  0.993432  0.985222   
2022-03-31 10:32:00+05:30       14  0.985222  0.979475  0.986043  0.984401   
2022-03-31 10:41:00+05:30       15  0.984401  0.983580  0.987685  0.987685   
2022-03-31 10:47:00+05:30       16  0.986864  0.983580  0.987685  0.983580   
2022-03-31 10:54:00+05:30       17  0.986043  0.983580  0.988506  0.987685   
2022-03-31 10:59:00+05:30       18  0.987685  0.987685  0.990148  0.987685   
2022-03-31 11:04:00+05:30       19  0.987685  0.987685  0.990969  0.989327   

                           Volume_n    SMA_10    SMA_20  VOL_SMA_20  \
datetime                                                              
2022-03-31 09:15:00+05:30  0.942294  0.996387  1.001232     6759.70   
2022-03-31 09:20:00+05:30  0.219142  0.996798  1.000534     6685.10   
2022-03-31 09:26:00+05:30  0.032628  0.996880  0.999836     6563.65   
2022-03-31 09:31:00+05:30  1.977610  0.996552  0.999015     7118.65   
2022-03-31 09:36:00+05:30  0.536796  0.996141  0.998563     7114.35   
2022-03-31 09:41:00+05:30  0.794370  0.995895  0.997988     6603.60   
2022-03-31 09:46:00+05:30  0.245809  0.996387  0.997537     6579.75   
2022-03-31 09:52:00+05:30  1.439246  0.995649  0.997003     6618.00   
2022-03-31 09:57:00+05:30  0.657269  0.995402  0.996429     6687.90   
2022-03-31 10:03:00+05:30  0.847390  0.994581  0.995649     6895.05   
2022-03-31 10:08:00+05:30  0.406754  0.993678  0.995033     5919.45   
2022-03-31 10:13:00+05:30  0.421028  0.992611  0.994704     5127.75   
2022-03-31 10:20:00+05:30  1.407402  0.991297  0.994089     5427.35   
2022-03-31 10:26:00+05:30  0.832017  0.990148  0.993350     5622.10   
2022-03-31 10:32:00+05:30  0.900568  0.988752  0.992447     5770.25   
2022-03-31 10:41:00+05:30  1.252575  0.988013  0.991954     6003.40   
2022-03-31 10:47:00+05:30  1.735879  0.986782  0.991585     5865.65   
2022-03-31 10:54:00+05:30  2.670173  0.986699  0.991174     6409.35   
2022-03-31 10:59:00+05:30  0.132081  0.986617  0.991010     5786.40   
2022-03-31 11:04:00+05:30  0.569581  0.987028  0.990805     5743.95   

                              RSI_14  ...  CMO_14_changelen_val  \
datetime                              ...                         
2022-03-31 09:15:00+05:30  46.868253  ...                     2   
2022-03-31 09:20:00+05:30  46.073312  ...                     1   
2022-03-31 09:26:00+05:30  45.246900  ...                     0   
2022-03-31 09:31:00+05:30  43.563883  ...                     0   
2022-03-31 09:36:00+05:30  45.737505  ...                     2   
2022-03-31 09:41:00+05:30  42.233930  ...                     1   
2022-03-31 09:46:00+05:30  43.401265  ...                     2   
2022-03-31 09:52:00+05:30  36.293232  ...                     1   
2022-03-31 09:57:00+05:30  36.293232  ...                     0   
2022-03-31

In [23]:
# pd.options.mode.use_inf_as_na = True
for t in feed.ndata:
    for d in feed.ndata[t]:
        if feed.ndata[t][d].isnull().values.any(): 
            feed.ndata[t][d]=feed.ndata[t][d].fillna(1)
            # print(t,d)
        if feed.ndata[t][d].isin([-np.inf,np.inf]).values.any():
            feed.ndata[t][d]=feed.ndata[t][d].replace([np.inf, -np.inf],1)
            # print(t,d)

In [24]:
with open(f'../algodata/realdata/datafeed_alldata_{RETAIN_OLD_FEATURES}_{ADD_FEATURES}.pkl','wb') as f: 
    pickle.dump(feed,f)

In [25]:
# with open('additional_utils/cols.pkl', 'wb') as f:
#     disc_wo_original = [col for col in discrete_cols if '_1_' not in col]
#     print(len(discrete_cols), len(disc_wo_original))
#     dic = {'pre_discrete_cols': pre_discrete_cols, 'discrete_cols': discrete_cols,
#            'discrete_wo_origninal_cols': disc_wo_original}
#     pickle.dump(dic, f)

In [26]:
# from math import isnan
# for d in feed.gdata:
#     for g in feed.gdata[d]:
#          for k in g: 
#                 if isnan(g[k]): g[k]=1

In [27]:
def get_alt_data_live():
    aD={'gdata':feed.gdata}
    return aD

In [28]:
agent=RLStratAgentDynFeatures(algorithm,monclass=Mon,soclass=StackedObservations,verbose=1,win=5,
                   metarl=True,myargs=(n_steps,use_alt_data), using_cols=using_cols)
agent.use_memory=True #depends on whether RL algorithm uses memory for state computation
agent.debug=False
if use_alt_data: agent.set_alt_data(alt_data_func=get_alt_data_live)

Using cpu device
Wrapping the env in a DummyVecEnv.


In [29]:
print(agent.using_cols)

['row_num', 'Open_n', 'High_n', 'Low_n', 'Close_n', 'Volume_n', 'SMA_10', 'SMA_20', 'VOL_SMA_20', 'RSI_14', 'BBL_5_2.0', 'BBM_5_2.0', 'BBU_5_2.0', 'BBB_5_2.0', 'BBP_5_2.0', 'MACD_12_26_9', 'MACDh_12_26_9', 'MACDs_12_26_9', 'VWAP_D', 'MOM_30', 'CMO_14', 'CMO_14_slope_1_polarity', 'Open_ma_1-Open_ma_10_val', 'Volume_ma_5_val', 'BBB_5_2.0_changelen_val', 'Open-Close_ma_1-Open-Close_ma_5_val', 'Volume_ma_20-Volume_ma_50_changelen_val', 'Open_n_ma_10_slope_5_changelen_polarity', 'Close_slope_1_polarity', 'RSI_14_ma_1_val', 'CMO_14_changelen_val', 'High_n-Low_n_ma_50_val', 'Open-Close_polarity', 'Open-High_ma_1-Open-High_ma_50_val', 'Open-Close_ma_1-Open-Close_ma_20_val', 'Close_n_ma_1-Close_n_ma_50_changelen_polarity', 'High_n_ma_1-High_n_ma_20_changelen_polarity', 'Open-High_ma_1-Open-High_ma_50_polarity']


In [30]:
if modelname and os.path.exists('./saved_models/'+modelname):
    print('Loading model')
    agent.load_model(filepath='./saved_models/'+modelname)

In [31]:
@aspectlib.Aspect
def my_decorator(*args, **kwargs):
    # print("Got called with args: %s kwargs: %s" % (args, kwargs))
    # result = yield
    # print(" ... and the result is: %s" % (result,))
    state,rew,done,exit_type = yield
    # args[0].policy.logL+=[(state.keys(),rew,done,exit_type)]
    args[0].policy.reward((rew,done,{'exit_type':exit_type}))
    return state,rew,done,exit_type

In [32]:
aspectlib.weave(Episode, my_decorator, methods='env_step')

In [33]:
bt=Backtest(feed,tickers=feed.tickers,add_features=False,target=5,stop=5,txcost=0.001,
            loc_exit=True,scan=True,topk=5,deploy=deploy,save_dfs=False,
            save_func=None)

In [34]:
agent.data_cols=continuing_cols
agent.error=False

In [35]:
print(agent.data_cols)

['row_num', 'Open_n', 'High_n', 'Low_n', 'Close_n', 'Volume_n', 'SMA_10', 'SMA_20', 'VOL_SMA_20', 'RSI_14', 'BBL_5_2.0', 'BBM_5_2.0', 'BBU_5_2.0', 'BBB_5_2.0', 'BBP_5_2.0', 'MACD_12_26_9', 'MACDh_12_26_9', 'MACDs_12_26_9', 'VWAP_D', 'MOM_30', 'CMO_14', 'CMO_14_slope_1_polarity', 'Open_ma_1-Open_ma_10_val', 'Volume_ma_5_val', 'BBB_5_2.0_changelen_val', 'Open-Close_ma_1-Open-Close_ma_5_val', 'Volume_ma_20-Volume_ma_50_changelen_val', 'Open_n_ma_10_slope_5_changelen_polarity', 'Close_slope_1_polarity', 'RSI_14_ma_1_val', 'CMO_14_changelen_val', 'High_n-Low_n_ma_50_val', 'Open-Close_polarity', 'Open-High_ma_1-Open-High_ma_50_val', 'Open-Close_ma_1-Open-Close_ma_20_val', 'Close_n_ma_1-Close_n_ma_50_changelen_polarity', 'High_n_ma_1-High_n_ma_20_changelen_polarity', 'Open-High_ma_1-Open-High_ma_50_polarity', 'Date', 'datetime']


In [36]:
def run_btworld():
    global bt,feed,agent
    while agent.training and not agent.error:
        bt.run_all(tickers=feed.tickers,model=agent,verbose=False)

In [37]:
agent.start(training_steps=training_steps)

In [38]:
btworldthread=Thread(target=run_btworld,name='btworld')
btworldthread.start()

In [39]:
def check_bt_training_status():
    threadL=[thread.name for thread in threading.enumerate()]
    # print(threadL)
    if 'monitor' not in threadL and 'btworld' not in threadL:
        print(f'Training Over after {agent.model.num_timesteps} steps')
        return False
    else:
        print(f'Model Training for {agent.model.num_timesteps} steps')
        return True

---------------------------------
| rollout/           |          |
|    ep_len_mean     | 4.22     |
|    ep_rew_mean     | -0.182   |
| time/              |          |
|    fps             | 60       |
|    iterations      | 1        |
|    time_elapsed    | 33       |
|    total_timesteps | 2048     |
---------------------------------


In [40]:
while check_bt_training_status():
    time.sleep(2)

Model Training for 3451 steps
Model Training for 3571 steps
Model Training for 3679 steps
Model Training for 3796 steps
Model Training for 3935 steps
Model Training for 4075 steps
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 5.08        |
|    ep_rew_mean          | 0.257       |
| time/                   |             |
|    fps                  | 61          |
|    iterations           | 2           |
|    time_elapsed         | 66          |
|    total_timesteps      | 4096        |
| train/                  |             |
|    approx_kl            | 0.009984883 |
|    clip_fraction        | 0.125       |
|    clip_range           | 0.2         |
|    entropy_loss         | -3.29       |
|    explained_variance   | -0.0884     |
|    learning_rate        | 0.0003      |
|    loss                 | 1.29        |
|    n_updates            | 10          |
|    policy_gradient_loss | -0.0163     |
|    value_loss       

KeyboardInterrupt: 

In [41]:
# Save learned model
# modelname=''
if modelname: torch.save(agent.model.policy.state_dict(),'./saved_models/'+modelname)

## Training Curves

In [42]:
if not script:
    import pandas as pd
    df=pd.read_csv('/tmp/aiagents.monitor.csv',comment='#')

In [43]:
if not script:
    import plotly.express as px
    px.line(df['r'].rolling(window=100).mean().values).show()

-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 2.34        |
|    ep_rew_mean          | 0.18        |
| time/                   |             |
|    fps                  | 37          |
|    iterations           | 221         |
|    time_elapsed         | 12194       |
|    total_timesteps      | 452608      |
| train/                  |             |
|    approx_kl            | 0.018423185 |
|    clip_fraction        | 0.101       |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.798      |
|    explained_variance   | 0.0787      |
|    learning_rate        | 0.0003      |
|    loss                 | 1.78        |
|    n_updates            | 2200        |
|    policy_gradient_loss | -0.00555    |
|    value_loss           | 3.46        |
-----------------------------------------


-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 2.17        |
|    ep_rew_mean          | 0.425       |
| time/                   |             |
|    fps                  | 37          |
|    iterations           | 222         |
|    time_elapsed         | 12265       |
|    total_timesteps      | 454656      |
| train/                  |             |
|    approx_kl            | 0.017664338 |
|    clip_fraction        | 0.111       |
|    clip_range           | 0.2         |
|    entropy_loss         | -0.775      |
|    explained_variance   | 0.0732      |
|    learning_rate        | 0.0003      |
|    loss                 | 1.12        |
|    n_updates            | 2210        |
|    policy_gradient_loss | -0.00527    |
|    value_loss           | 3.52        |
-----------------------------------------
-----------------------------------------
| rollout/                |             |
|    ep_len_mean          | 2.29  